## Перевод среды на gymnasium

In [14]:
import gymnasium as gym
from gymnasium import spaces

class TicTacToeEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    
    symbols = ['O', ' ', 'X']

    def __init__(self):
        super().__init__()
        self.action_space = spaces.Discrete(9)
        self.observation_space = spaces.Discrete(9 * 3 * 2)
        self.reset()

    def step(self, action):
        finished = False
        score = 0

        player, cell = action  # player - игрок (1 или -1), cell - номер клетки

        board = self.state['board']
        current_cell = board[cell]
        current_player = self.state['current_turn']
        if current_cell != 0:  # Клетка занята
            print(f"Некорректный ход: Клетка {cell} уже занята.")
            finished = True
            score = -1 * current_player
        elif player != current_player:  # Ход сделан не тем игроком
            print(f"Некорректный ход: игрок {player} не на очереди.")
            finished = True
            score = -1 * current_player
        else:
            board[cell] = player
            self.state['current_turn'] = -player

        for row in range(3):
            # Проверяем строки и столбцы
            if (board[row * 3] == player and board[row * 3 + 1] == player and board[row * 3 + 2] == player) or \
               (board[row] == player and board[row + 3] == player and board[row + 6] == player):
                score = player
                finished = True
                break

        # Проверяем диагонали
        if (board[0] == player and board[4] == player and board[8] == player) or \
           (board[2] == player and board[4] == player and board[6] == player):
            score = player
            finished = True
                
        return self.state, score, finished, {}

    def reset(self):
        self.state = {
            'board': [0] * 9,  # Поле 3x3
            'current_turn': 1  # Начинает первый игрок
        }
        return self.state, {}

    def render(self, close=False):
        if close:
            return
        print("Current turn:", self.symbols[self.state['current_turn'] + 1])
        for idx in range(9):
            print(self.symbols[self.state['board'][idx] + 1], end=" ")
            if (idx % 3) == 2:
                print()

    def available_moves(self):
        moves = []
        for idx in range(9):
            if self.state['board'][idx] == 0:
                player = self.state['current_turn']
                moves.append([player, idx])
        return moves

## Агент
Агент - система, которая взаимодействует с окружающей средой, чтобы достичь определенной цели. Задача агента: выработка стратегии, которая максимизирует награду в долгосрочной перспективе.
Роль агента: агент принимает решение, основываясь на текущем состоянии среды и получает обратную свзяь от среды.
Функционал агента: принятие решения - использование алгоритмов или стратегий для дальнейшего принятия решения; обучение - обновление знаний или стратегий основываясь на полученный опыт; интерактивность - адаптация к изменениям в среде.

In [15]:
import random

# Агент, взаимодействующий со средой для выбора стратегий на основе доступных ходов
class GameAgent:
    def __init__(self, token):
        self.token = token  # Символ игрока (1 - X, -1 - O)
    
    def select_move(self, moves):
        return random.choice(moves)  # Выбор случайного хода из доступных

## Основной цикл обучения

In [17]:
# Основной цикл обучения агента

# Создаём игровую среду
game_env = TicTacToeEnv()

# Создаём агента, играющего крестиками
player_agent = GameAgent(token=1)

total_episodes = 100  # Количество эпизодов (игр) для обучения
reward_history = []  # Для хранения результатов эпизодов

# Переменная для отслеживания символа текущего игрока
initial_turn = 1

for episode in range(total_episodes):
    # Сбрасываем состояние игры перед началом нового эпизода
    game_state, _ = game_env.reset()

    # Общая награда за эпизод
    episode_reward = 0

    # Флаг завершения игры
    game_finished = False
    current_turn = initial_turn

    # Игровой цикл (до 9 ходов для поля 3x3)
    for move_count in range(9): 
        moves = game_env.available_moves()  # Получаем доступные ходы

        # Если ходов нет, игра завершается
        if not moves:
            break

        # Агент делает выбор
        chosen_move = player_agent.select_move(moves) if len(moves) > 1 else moves[0]

        # Выполняем ход и обновляем состояние игры
        next_state, reward, game_finished, _ = game_env.step(chosen_move)
        episode_reward += reward
        game_state = next_state

        # Отображаем текущее состояние
        game_env.render()

        # Если игра завершена, выходим
        if game_finished:
            break

        current_turn = -current_turn  # Смена игрока

    reward_history.append(episode_reward)

    # Выводим статистику
    print(f"Эпизод {episode + 1}, Итоговая награда: {episode_reward}")
    avg_reward = sum(reward_history) / len(reward_history)
    print(f"Средняя награда: {avg_reward:.2f}")

Current turn: O
      
      
X     
Current turn: X
      
      
X O   
Current turn: O
      
X     
X O   
Current turn: X
  O   
X     
X O   
Current turn: O
  O   
X   X 
X O   
Current turn: X
  O   
X   X 
X O O 
Current turn: O
X O   
X   X 
X O O 
Эпизод 1, Итоговая награда: 1
Средняя награда: 1.00
Current turn: O
      
      
X     
Current turn: X
      
      
X O   
Current turn: O
      
      
X O X 
Current turn: X
  O   
      
X O X 
Current turn: O
X O   
      
X O X 
Current turn: X
X O   
O     
X O X 
Current turn: O
X O   
O   X 
X O X 
Current turn: X
X O O 
O   X 
X O X 
Current turn: O
X O O 
O X X 
X O X 
Эпизод 2, Итоговая награда: 1
Средняя награда: 1.00
Current turn: O
    X 
      
      
Current turn: X
    X 
      
  O   
Current turn: O
    X 
      
X O   
Current turn: X
    X 
    O 
X O   
Current turn: O
    X 
  X O 
X O   
Эпизод 3, Итоговая награда: 1
Средняя награда: 1.00
Current turn: O
      
    X 
      
Current turn: X
      
O   X 
